In [1]:
%load_ext autoreload
%autoreload 2

In [2]:
import os
import sys
import numpy as np
import pandas as pd
import datetime
import seaborn as sns
import ogb
from tqdm import tqdm
import hiplot as hip
from copy import deepcopy
import datetime

In [3]:
import torch
from torch_geometric.data import Data
from torch_geometric.loader import DataLoader
from torch.utils.data import Subset, TensorDataset

In [4]:
cwd = os.getcwd()
print(cwd)

/cluster/home/skyriakos/chemprop_run/git/notebooks


In [5]:
os.chdir('..')
import deepadr
from deepadr.dataset import *
from deepadr.utilities import *
from deepadr.run_workflow import *
from deepadr.chemfeatures import *
from deepadr.hyphelper import *
# from deepadr.model_gnn import GCN as testGCN
from deepadr.model_gnn_ogb import GNN, DeepAdr_SiameseTrf, ExpressionNN
# from deepadr.model_attn_siamese import *
from ogb.graphproppred import Evaluator
os.chdir(cwd)

In [6]:
from rdkit.Chem.Draw import IPythonConsole
from rdkit.Chem import Draw

In [7]:
# from tdc.single_pred import Tox
# from tdc.multi_pred import DDI

In [8]:
rawdata_dir = '../data/raw/'
processed_dir = '../data/processed/'
up_dir = '..'

In [9]:
report_available_cuda_devices()

number of GPUs available: 8
cuda:0, name:GeForce GTX 1080 Ti
total memory available: 10.91650390625 GB
total memory allocated on device: 0.0 GB
max memory allocated on device: 0.0 GB
total memory cached on device: 0.0 GB
max memory cached  on device: 0.0 GB

cuda:1, name:GeForce GTX 1080 Ti
total memory available: 10.91650390625 GB
total memory allocated on device: 0.0 GB
max memory allocated on device: 0.0 GB
total memory cached on device: 0.0 GB
max memory cached  on device: 0.0 GB

cuda:2, name:GeForce GTX 1080 Ti
total memory available: 10.91650390625 GB
total memory allocated on device: 0.0 GB
max memory allocated on device: 0.0 GB
total memory cached on device: 0.0 GB
max memory cached  on device: 0.0 GB

cuda:3, name:GeForce GTX 1080 Ti
total memory available: 10.91650390625 GB
total memory allocated on device: 0.0 GB
max memory allocated on device: 0.0 GB
total memory cached on device: 0.0 GB
max memory cached  on device: 0.0 GB

cuda:4, name:GeForce GTX 1080 Ti
total memory av

In [10]:
n_gpu = torch.cuda.device_count()
n_gpu

8

In [11]:
device_cpu = get_device(to_gpu=False)
# device_gpu = get_device(True, index=0)

# fdtype = torch.float32

In [12]:
print("torch:", torch.__version__)
print("CUDA:", torch.version.cuda)
print(sys.version)

torch: 1.9.1
CUDA: 11.1
3.9.9 | packaged by conda-forge | (main, Dec 20 2021, 02:41:03) 
[GCC 9.4.0]


In [13]:
# print(torch.cuda.memory_summary(device=device_gpu))

### Preparing dataset 

In [14]:
# TDC Tox
DSdataset_name = 'MatchMakerDrugComb' #'OncoPolyPharmacology' #'DrugComb'

#fname_suffix = ds_config["fname_suffix"]
similarity_types = ['chem']
kernel_option = 'sqeuclidean'
data_fname = 'data_v1'
# interact_matfname = ds_config["interact_matfname"]
# exp_iden = 'simtypeall'
# ddi_interaction_labels_pth = ds_config["ddi_interaction_labels_pth"]

# up_dir, processed_dir, DSdataset_name, data_fname

In [15]:
targetdata_dir = create_directory(os.path.join(processed_dir, DSdataset_name, data_fname))
targetdata_dir_raw = create_directory(os.path.join(targetdata_dir, "raw"))
targetdata_dir_processed = create_directory(os.path.join(targetdata_dir, "processed"))
# # ReaderWriter.dump_data(dpartitions, os.path.join(targetdata_dir, 'data_partitions.pkl'))
print(targetdata_dir)

path_current_dir /cluster/home/skyriakos/chemprop_run/git/deepadr
path_current_dir /cluster/home/skyriakos/chemprop_run/git/deepadr
path_current_dir /cluster/home/skyriakos/chemprop_run/git/deepadr
/cluster/home/skyriakos/chemprop_run/git/data/processed/MatchMakerDrugComb/data_v1


In [16]:
%%time

# Make sure to first run the "data_generation" notebook first

dataset = MoleculeDataset(root=targetdata_dir)

CPU times: user 7.02 ms, sys: 710 ms, total: 717 ms
Wall time: 1.37 s


In [17]:
# print()
# print(f'Dataset: {dataset}:')
# print('====================')
# print(f'Number of graphs: {len(dataset)}')
# print(f'Number of features: {dataset.num_features}')
# print(f'Number of classes: {dataset.num_classes}')

# # data0 = dataset[0]  # Get the first graph object.

# # print()
# # print(data)
# # print('=============================================================')

# # # Gather some statistics about the first graph.
# # print(f'Number of nodes: {data.num_nodes}')
# # print(f'Number of edges: {data.num_edges}')
# # print(f'Average node degree: {data.num_edges / data.num_nodes:.2f}')
# # print(f'Contains isolated nodes: {data.contains_isolated_nodes()}')
# # print(f'Contains self-loops: {data.contains_self_loops()}')
# # print(f'Is undirected: {data.is_undirected()}')

In [18]:
# data0

In [19]:
# data0.expression.shape

In [20]:
# data0.y

In [21]:
# dataset.tensors[1]

In [22]:
# used_dataset = dataset

# If you want to use a smaller subset of the dataset for testing
smaller_dataset_len = int(len(dataset)/1)
used_dataset = dataset[:smaller_dataset_len]

In [23]:
type(used_dataset)

deepadr.dataset.MoleculeDataset

In [24]:
fold_partitions = get_stratified_partitions(used_dataset.data.y[:smaller_dataset_len],
                                            num_folds=5, valid_set_portion=0.1, random_state=42)

fold_num: 0
train data
class: 0 norm count: 0.9410649119278182
class: 1 norm count: 0.058935088072181833
validation data
class: 0 norm count: 0.9410395655546936
class: 1 norm count: 0.05896043444530644
test data
class: 0 norm count: 0.9410395655546936
class: 1 norm count: 0.05896043444530644

-------------------------
fold_num: 1
train data
class: 0 norm count: 0.9410513914630116
class: 1 norm count: 0.05894860853698835
validation data
class: 0 norm count: 0.9410395655546936
class: 1 norm count: 0.05896043444530644
test data
class: 0 norm count: 0.941088238336609
class: 1 norm count: 0.05891176166339092

-------------------------
fold_num: 2
train data
class: 0 norm count: 0.9410513914630116
class: 1 norm count: 0.05894860853698835
validation data
class: 0 norm count: 0.9410395655546936
class: 1 norm count: 0.05896043444530644
test data
class: 0 norm count: 0.941088238336609
class: 1 norm count: 0.05891176166339092

-------------------------
fold_num: 3
train data
class: 0 norm count: 

In [25]:
# train_val_test_frac = [0.7, 0.1, 0.2]
# assert sum(train_val_test_frac) == 1

# torch.manual_seed(42)
# used_dataset = used_dataset.shuffle()

# num_train = round(train_val_test_frac[0] * len(used_dataset)) 
# num_trainval = round((train_val_test_frac[0]+train_val_test_frac[1]) * len(used_dataset))

# train_dataset = used_dataset[:num_train]
# val_dataset = used_dataset[num_train:num_trainval]
# test_dataset = used_dataset[num_trainval:]

In [26]:
# train_dataset = Subset(used_dataset, fold_partitions[0]['train'])
# val_dataset = Subset(used_dataset, fold_partitions[0]['validation'])
# test_dataset = Subset(used_dataset, fold_partitions[0]['test'])

In [27]:
# print(f'Number of training graphs: {len(train_dataset)}')
# print(f'Number of val graphs: {len(val_dataset)}')
# print(f'Number of test graphs: {len(test_dataset)}')

In [28]:
print("Number of training graphs: "+ str(len(fold_partitions[0]['train'])))
print("Number of training graphs: "+ str(len(fold_partitions[0]['validation'])))
print("Number of training graphs: "+ str(len(fold_partitions[0]['test'])))


Number of training graphs: 69602
Number of training graphs: 7734
Number of training graphs: 19335


In [29]:
# print(dataset.num_classes)

In [30]:
# training params
tp = {
    "batch_size" : 512,
    "num_epochs" : 200,
    
    "emb_dim" : 300,
    "gnn_type" : "gatv2",
    "num_layer" : 5,
    "graph_pooling" : "mean", #attention
    
    "input_embed_dim" : None,
    "num_attn_heads" : 2,
    "num_transformer_units" : 1,
    "p_dropout" : 0.3,
#     "nonlin_func" : nn.ReLU(),
    "mlp_embed_factor" : 2,
    "pooling_mode" : 'attn',
    "dist_opt" : 'cosine',

    "base_lr" : 3e-5, #3e-4
    "max_lr_mul": 5,
    "l2_reg" : 1e-7,
    "loss_w" : 0.1,
    "margin_v" : 1.,

    "expression_dim" : 64,
    "expression_input_size" : 972,
    "exp_H1" : 500,
    "exp_H2" : 400
}

In [31]:
# input_embed_dim = [128]
num_attn_heads = [2,4] # 2,4
num_transformer_units = [1]
p_dropout = [0.3]
# nonlin_func = [nn.ReLU()]
# mlp_embed_factor = [2]
# pooling_mode = ['attn']
# dist_opt = ['cosine']
l2_reg = [0] #0
batch_size = [512]
# num_epochs = [200]
loss_w = [0.05] # 0.05, 
# base_lr = [3e-2, 3e-3, 3e-4, 3e-5, 3e-6, 3e-7]
max_lr_mul = [3,5,10,15]


In [37]:
hp_names = ["num_attn_heads",
            "p_dropout",
            "l2_reg",
            "loss_w",
           "num_transformer_units",
           "batch_size",
           "max_lr_mul"]

In [38]:
[globals()[i] for i in hp_names]

[[2, 4], [0.3], [0], [0.05], [1, 2], [64, 512]]

In [39]:
hyperparam_space = list(itertools.product(*[globals()[i] for i in hp_names]))
print(len(hyperparam_space))

8


In [40]:
hyperparam_space[0]

(2, 0.3, 0, 0.05, 1, 64)

In [41]:
targetdata_dir_exp = create_directory(os.path.join(targetdata_dir, "experiments"))

path_current_dir /cluster/home/skyriakos/chemprop_run/git/deepadr


In [42]:
# device_gpu = get_device(True, index=0)
# exp_dir = create_directory(os.path.join(targetdata_dir_exp, "exp0"))
# tphp = generate_tp_hp(tp, hyperparam_space[0], hp_names)
# partition = fold_partitions[0]

In [43]:
# run_exp(tphp, device_gpu, exp_dir,partition=fold_partitions[0], used_dataset=used_dataset)

In [44]:
def spawn_q_process(q_process):
    print(">>> spawning hyperparam search process")
    q_process.start()
    
def join_q_process(q_process):
    q_process.join()
    print("<<< joined hyperparam search process")
    
def create_q_process(queue, used_dataset, gpu_num, tphp, exp_dir, partition): #
#     fold_gpu_map = {0:gpu_num}
    return mp.Process(target=deepadr.hyphelper.run_exp, args=(queue, used_dataset, gpu_num, tphp, exp_dir, partition)) #

In [45]:
import torch.multiprocessing as mp
mp.set_start_method("spawn", force=True)

queue = mp.Queue()
q_processes = []

partition = fold_partitions[0]

print("Start: " + datetime.datetime.now().strftime('%Y-%m-%d_%H-%M-%S'))

for q_i in range(min(n_gpu, len(hyperparam_space))):
#     device_gpu = get_device(True, index=q_i)
    time_stamp = datetime.datetime.now().strftime('%Y-%m-%d_%H-%M-%S')
    exp_dir = create_directory(os.path.join(targetdata_dir_exp, "exp_"+str(q_i)+"_"+time_stamp))
    tphp = generate_tp_hp(tp, hyperparam_space[q_i], hp_names)
    
    q_process = create_q_process(queue, used_dataset, q_i, tphp, exp_dir, partition)
    q_processes.append(q_process)
    spawn_q_process(q_process)

spawned_processes = n_gpu
    
for q_i in range(len(hyperparam_space)):
    join_q_process(q_processes[q_i])
    released_gpu_num = queue.get()
    print("released_gpu_num:", released_gpu_num)
    if(spawned_processes < len(hyperparam_space)):
#         device_gpu = get_device(True, index=q_i)
        time_stamp = datetime.datetime.now().strftime('%Y-%m-%d_%H-%M-%S')
        exp_dir = create_directory(os.path.join(targetdata_dir_exp, "exp_"+str(q_i)+"_"+time_stamp))
        tphp = generate_tp_hp(tp, hyperparam_space[q_i], hp_names)

        q_process = create_q_process(queue, used_dataset, released_gpu_num, tphp, exp_dir, partition)
        q_processes.append(q_process)
        spawn_q_process(q_process)
        spawned_processes = spawned_processes + 1

Start: 2022-01-13_17-52-11
path_current_dir /cluster/home/skyriakos/chemprop_run/git/deepadr
>>> spawning hyperparam search process
path_current_dir /cluster/home/skyriakos/chemprop_run/git/deepadr
>>> spawning hyperparam search process
path_current_dir /cluster/home/skyriakos/chemprop_run/git/deepadr
>>> spawning hyperparam search process
path_current_dir /cluster/home/skyriakos/chemprop_run/git/deepadr
>>> spawning hyperparam search process
path_current_dir /cluster/home/skyriakos/chemprop_run/git/deepadr
>>> spawning hyperparam search process
gpu: cuda:0
updated
num classes: 2
=====Epoch 0
Training...
gpu: cuda:1
updated
num classes: 2
=====Epoch 0
Training...


Iteration:   0%|          | 0/136 [00:00<?, ?it/s]

gpu: cuda:2
updated
num classes: 2
=====Epoch 0
Training...


Iteration:   0%|          | 0/1088 [00:00<?, ?it/s]

gpu: cuda:3
updated
num classes: 2
=====Epoch 0
Training...


...

{'Train':  best_epoch_indx:298
 auc:0.92686580926824 
 apur:0.5839491960203008 
 f1:0.35903578379997003 
 precision:0.22572952620018827 
 recall:0.8768893222818137 
, 'Validation':  best_epoch_indx:298
 auc:0.9050760703972077 
 apur:0.5761538333365007 
 f1:0.34165923282783234 
 precision:0.21444568868980962 
 recall:0.8399122807017544 
, 'Test':  best_epoch_indx:298
 auc:0.9128042213255039 
 apur:0.5443938410353689 
 f1:0.3473399458972047 
 precision:0.21861520998864925 
 recall:0.8447368421052631 
}
=====Epoch 299
Training...


Iteration:   0%|          | 4/1088 [00:00<00:34, 31.81it/s]

Evaluating...


Iteration: 100%|██████████| 121/121 [00:02<00:00, 45.04it/s]


{'Train':  best_epoch_indx:299
 auc:0.9267612093895734 
 apur:0.585729384543626 
 f1:0.33679066980131844 
 precision:0.20766300949349098 
 recall:0.8905411994149196 
, 'Validation':  best_epoch_indx:299
 auc:0.9063610351793197 
 apur:0.5802740270787358 
 f1:0.32138442521631644 
 precision:0.197869101978691 
 recall:0.8552631578947368 
, 'Test':  best_epoch_indx:299
 auc:0.9131873755562305 
 apur:0.5433376365792344 
 f1:0.3275459098497495 
 precision:0.2022680412371134 
 recall:0.8605263157894737 
}
Finished training!
Best validation score: 0.5802740270787358
Test score: 0.5433376365792344
<<< joined hyperparam search process
released_gpu_num: 2
<<< joined hyperparam search process
released_gpu_num: 6


In [46]:
print("End: " + datetime.datetime.now().strftime('%Y-%m-%d_%H-%M-%S'))


End: 2022-01-14_04-48-23


In [47]:
import glob
exp_dirs = glob.glob(targetdata_dir_exp+"/exp_*")
len(exp_dirs)

24

In [48]:
exp_results = []

for edir in exp_dirs:
    hp = pd.read_json(edir + "/hyperparameters.json", typ="Series").to_dict()
    hp['maxTestAUPR'] = pd.read_csv(edir + "/curves.csv").test.max()
    exp_results.append(hp)

In [49]:
hip.Experiment.from_iterable(exp_results).display(force_full_width=False)

<IPython.core.display.Javascript object>